# Instalacion de librerias

In [ ]:
pip install pulp

     |████████████████████████████████| 40.6MB 83kB/s 


# Carga de librerias

In [ ]:
import pandas as pd
import numpy as np
from scipy.optimize import linprog
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable

In [ ]:
try:
    # settings colab:
    from google.colab import drive
except ModuleNotFoundError:    
    print("Ha ocurrido un error")

In [ ]:
try:
    drive.mount('/content/drive')
except Exception:    
    print("Ha ocurrido un error") 

Mounted at /content/drive


# Ejercicio 1

En un taller metalúrgico se fabrican dos tipos de piezas A y B, que deben seguir los siguientes
procesos:
1. Estampado en hojas metálicas
2. Soldado
3. Pintado

La operación de estampado consiste en preparar partes idénticas que luego serán soldadas de a
pares, formando la pieza A. El mismo proceso se realiza para la pieza B.
Los insumos de equipos son los siguientes, para la realización de cada una de las operaciones
(expresados en segundos por pieza):

Guia 1 - Ejercicio 1.jpg

La utilidad unitaria es de \$ 4 para la pieza A y \$ 3 para la pieza B. Se desea establecer el
programa semanal de producción que maximice la utilidad del taller con respecto a las piezas
consideradas.

## Con Scipy

Se define la funcion objetivo y las restricciones

Observaciones de Scipy: 
* Solamente se pueden resolver problemas de Mínimización
* No acepta restricciones de Mayor o igual (>=)

En este problema como es de Maximizacion, se cambia a minimizacion de la siguiente forma:
* max z = 4 * x + 3 * y -----> es equivalente a ------> min z = -4 * x - 3 * y

In [ ]:
obj = [-4, -3] # se cambian de signos para pasar de maximizacion a minimizacion
#      ─┬  ─┬
#       │   └┤ coeficiente para y
#       └────┤ coeficiente para x

lhs_ineq = [[ 3, 8],  # Coeficientes estampado lado izquierdo
            [12, 6],  # Coeficientes soldado lado izquierdo
            [ 9, 9]]  # Coeficientes pintado ecuacion coeficientes lado izquierdo

rhs_ineq = [48000,  # Estampado ecuacion lado derecho
            42000,  # Soldado lado derecho
            36000]  # Pintado lado derecho

Se definen los limites de las variables x e y. Esta definicion es redundante ya que son los valores por defecto

In [ ]:
bnd = [(0, float("inf")),  # Limite de x
         (0, float("inf"))]  # Limite of y

Optimizacion y resolucion del problema

In [ ]:
opt = linprog(c=obj, A_ub=lhs_ineq, b_ub=rhs_ineq,
             bounds=bnd, method="revised simplex")
opt

     con: array([], dtype=float64)
     fun: -15000.0
 message: 'Optimization terminated successfully.'
     nit: 2
   slack: array([31000.,     0.,     0.])
  status: 0
 success: True
       x: array([3000., 1000.])

Valores que se obtienen son:
* con: Residuos de restricciones de igualdad
* fun: Valor optimo de la función objetivo en la igualdad (si es que existe)
* message: Status de la solucion
* nit: Numero de iteraciones necesarias para realizar el calculo
* slack: Valores de las variables slack
* status: Numero entero entre 0 y 4 que muestra el resultado de la solucion:
 * 0: solucion optima
 * 1: iteracion limitada
 * 2: solucion degenerada
 * 3: solucion irrestrica
 * 4: se encuentran dificultadas numericas
* success: Variable booleana que indica si se alcanzo la solucion optima
* x: NumPy array que continiene los valores optimos para las variables de decision

## Con Pulp

Se inicializa una instancia de LpProblem:
* Maximizacion: sense = LpMaximize o -1
* Minimizacion: sense = LpMinimize o 1 (es la opcion que viene por default)

Creacion del modelo

In [ ]:
model = LpProblem(name="Maximizacion_Beneficio_Fabrica", sense=LpMaximize)

Inicializacion de variables

In [ ]:
A = LpVariable(name="A", lowBound=0)
B = LpVariable(name="B", lowBound=0)

Restricciones

In [ ]:
random_demanda = rnd()

In [ ]:
model += ( 3 * A + 8 * B <= 48000, "estampado")
model += (12 * A + 6 * B <= 42000, "soldado")
model += ( 9 * A + 9 * B <= 36000, "pintado")

Funcion Objetivo

In [ ]:
obj_func = 4 * A + 3 * B
model += obj_func

In [ ]:
model

Maximizacion_Beneficio_Fabrica:
MAXIMIZE
4*A + 3*B + 0
SUBJECT TO
estampado: 3 A + 8 B <= 48000

soldado: 12 A + 6 B <= 42000

pintado: 9 A + 9 B <= 36000

VARIABLES
A Continuous
B Continuous

Resolucion del problema

In [ ]:
status = model.solve()

In [ ]:
print(f"status: {model.status}, {LpStatus[model.status]}")

status: 1, Optimal


In [ ]:
print(f"objective: {model.objective.value()}")

objective: 15000.0


In [ ]:
for var in model.variables():
    print(f"{var.name}: {var.value()}")

A: 3000.0
B: 1000.0


In [ ]:
for name, constraint in model.constraints.items():
    print(f"{name}: {constraint.value()}")

estampado: -31000.0
soldado: 0.0
pintado: 0.0


## Con Pulp - Lectura de dataframes

Lectura del dataframe

In [ ]:
df_insumos = pd.read_excel('/content/drive/My Drive/Guia 1 - Ejercicio 1/Guia 1 - Ejercicio 1 insumos.xlsx')

In [ ]:
df_insumos

Operacion  Pieza_A  Pieza_B  Tiempo_Disponible_seg_por_semana
0  Estampado        3        8                             48000
1    Soldado       12        6                             42000
2    Pintado        9        9                             36000

In [ ]:
df_utilidad = pd.read_excel('/content/drive/My Drive/Guia 1 - Ejercicio 1/Guia 1 - Ejercicio 1 utilidad.xlsx')

In [ ]:
df_utilidad

Pieza_A  Pieza_B
0        4        3

Inicializacion de variables

In [ ]:
A = LpVariable(name="A", lowBound=0)
B = LpVariable(name="B", lowBound=0)

Creacion del modelo

In [ ]:
model_2 = LpProblem(name="Maximizacion_Beneficio_Fabrica", sense=LpMaximize)

Definicion de restricciones
* la funcion lp realiza una suma de los elementos que hay dentro
* luego de la coma se agrega como string el nombre de cada una de las variables

In [ ]:
for i in range(len(df_insumos)):
    model_2 += lpSum(df_insumos['Pieza_A'][i] * A + df_insumos['Pieza_B'][i] * B) <= df_insumos['Tiempo_Disponible_seg_por_semana'][i], str(df_insumos['Operacion'][i])

Funcion objetivo

In [ ]:
obj_func_2 = lpSum(df_utilidad['Pieza_A'] * A + df_utilidad['Pieza_B'] * B)
model_2 += obj_func_2

In [ ]:
obj_func_2

4*A + 3*B + 0

In [ ]:
status_2 = model_2.solve()

In [ ]:
print(f"status: {model_2.status}, {LpStatus[model_2.status]}")

status: 1, Optimal


In [ ]:
print(f"objective: {model_2.objective.value()}")

objective: 15000.0


In [ ]:
for var in model_2.variables():
    print(f"{var.name}: {var.value()}")

A: 3000.0
B: 1000.0


In [ ]:
for name, constraint in model_2.constraints.items():
    print(f"{name}: {constraint.value()}")

Estampado: -31000.0
Soldado: 0.0
Pintado: 0.0
